# The Universe in a Single Arrow
## A live dive into the Lambda Calculus

JSHeroes 2019

🐦 **[@AnjanaVakil](https://twitter.com/AnjanaVakil)** 
  
🗺️ [Mapbox](http://www.mapbox.com), 🗣️ [Mozilla TechSpeakers](https://wiki.mozilla.org/TechSpeakers), 💡 [Recurse Center](https://www.recurse.com), 👩🏽‍💻 [Outreachy](http://www.outreachy.org)

# The whatta calculus?


## Lambda (𝛌) Calculus
* Mathematical formalism
* Invented by this hero (Alonzo Church) starting 1932:
  ![Alonzo Church](https://upload.wikimedia.org/wikipedia/en/a/a6/Alonzo_Church.jpg)
* Universal model of computation (Turing-complete) (NBD)


| ** Lambda function (𝛌) ** | ** Arrow function (`=>`) **
--- | --- |  ---
*used for* | thinking | programming
*inputs*   | 1 | 0+
*outputs*  | 1 | 0+
*side effects?* | no way!  | maybe

### If we treat `=>` like 𝛌, **what can we do** with it?


_Spoiler alert:_ EVERYTHING!!!

#### Disclaimer: 

Experimentation, sillyness, & learning ahead! 😜
    
For useful programming tips, please make a U-turn 🖖


 | ** Lambda function (𝛌) ** | ** Arrow function (`=>`)**
--- | --- |  ---
*making one*<br>*("abstraction")*|  λx.x | `x => x`
 *faking multiple args*          |  λx.λy.x+y | ~~`(x, y) => x + y`~~<br>`x => y => x + y`
*using one*<br>*("application")* | (λx.λy.x+y) 5 1<br>> 5+1<br>> 6 | `(x => y => x + y)(5)(1)`*<br>*> `5+1`<br>> `6`


## Numbers!

Counting is fun!

What can we count if all we have are functions?

We can count **function applications** (calls)!

In [1]:
var zero = f => x => x;

In [2]:
var one = f => x => f(x);

In [3]:
var two = f => x => f(f(x));

In [4]:
var three = f => x => f(f(f(x)));

### Wait... are you sure these are numbers?

In [5]:
// cheating! but just for sanity checks...

var toNumber = n => n(i => i+1)(0) ;

In [6]:
toNumber(two);

2

## Higher numbers!

Successor function: given a number, get the next number

In [7]:
var succ = n => f => x => f(n(f)(x));

In [8]:
var four = succ(three);
var five = succ(succ(three));
var six = succ(succ(succ(three)));
var seven = succ(succ(succ(succ(three))));

In [9]:
toNumber(seven);

7

In [10]:
var eight = seven(succ)(one);
toNumber(eight);

8

Yay! We have numbers! 

aka...

### Church Numerals

## Arithmetic!

How can we add two numbers `n` and `m`, when numbers are call-counters?

Call the function `n` times, then call it `m` more times!

In [11]:
var add = n => m => f => x => m(f)(n(f)(x)); 

In [12]:
var four = add(one)(three);
toNumber(add(two)(three));

5

## Arithmetic!

What about multiplying `n` and `m`?

Call the function `n` times, `m` times over!

In [13]:
var mul = n => m => f => x => m(n(f))(x);

In [14]:
toNumber(mul(four)(three));

12

## Arithmetic!

What about `n` to the power of `m`?

In [15]:
var power = n => m => m(n);

In [16]:
toNumber(power(three)(four));

81

## A Deep Thought

> What's the answer to life, the universe, and everything?

In [17]:
var answer = add(two)(mul(four)(mul(two)(add(four)(one))));
toNumber(answer);

42

OK cool, we can do some (simple) math!

What else do we need to write programs?

## Booleans! Conditionals!

These go hand-in-hand: 

`<boolean> ? <then do this> : <else do this>`

    if <boolean>:
       then <do this>
    else:
       <do this>

In [18]:
var ifThenElse = bool => thn => els => bool(thn)(els);
var troo = thn => els => thn;
var falz = thn => els => els;

In [19]:
var tired = troo ;
var coffeesToday = ifThenElse(tired)(three)(one) ;
toNumber(coffeesToday);

3

## Logic!

In [20]:
// more cheating, just for simplicity's sake...
var toBoolean = bool => bool(true)(false) ;

toBoolean(falz);

false

In [21]:
var not = bool => thn => els => bool(els)(thn);

In [22]:
toBoolean(not(troo));

false

## Predicates!

In [23]:
var is_zero = n => n(_ => falz)(troo) ;

toBoolean(is_zero(zero));

true

In [24]:
var is_even = n => n(not)(troo) ;

toBoolean(is_even(zero));

true

## More logic!

In [25]:
var or = A => B => A(A)(B);

In [26]:
toBoolean(or(falz)(troo));

true

In [27]:
var and = A => B => A(B)(A);

In [28]:
toBoolean(and(falz)(troo));

false

Cool, we've got some data!

### What about data **structures**?

## Lists!

What can a list contain?

* Nothing (empty, aka `nil`)
* One thing
* Multiple things

We'll build lists out of **pairs** of two things

## Pairs!

In [29]:
var makePair = left => right => f => f(left)(right) ;

var getLeft = pair => pair(troo);
var getRight = pair => pair(falz);

In [30]:
toNumber(getRight(makePair(two)(three)));

3

## Lists!

A list will have the form: `(empty?, list_contents)`

In [31]:
var isEmpty = getLeft;

Only `nil` (the empty list) will have `troo` as left element, i.e. `empty?` === `troo`

(the right element doesn't really matter; let's make it `troo` too!)

In [32]:
var nil = makePair(troo)(troo) ;
toBoolean(isEmpty(nil));

true

## Lists!

To add a new item to a list, we prepend the item to the old list,
making the new list:

`(empty?=falz, (new_item, old_list))`

In [33]:
var prepend = item => list => makePair(falz)(makePair(item)(list));

Non-empty lists are composed of nested pairs, e.g.

`[3, 2, 1]` --> `(empty?=falz, (3,(2,(1,nil))))`

In [34]:
var singleItemList = prepend(one)(nil);  // (falz, (1,nil))
var multiItemList = prepend(three)(prepend(two)(singleItemList)); // (falz, (3,(2,(1,nil))))

## Lists!

So non-empty lists always have form: `(empty?=falz, (head,tail))`  

How can we get the `head` (1st item in list) & `tail` (rest of list) ? 

In [35]:
var head = list => getLeft(getRight(list));
var tail = list => getRight(getRight(list));

How can we select the `2` in our `multiItemList`? 

    (falz, (3,(2,(1,nil))))

In [36]:
toNumber(head(tail(multiItemList)));

2

Yay, look at all the stuff we've got!

* Data
    * (natural) numbers
    * booleans
* Arithmetic
* Logic & Control flow

Representing data this way is called...

### Church Encoding

## There's so much more we could do!


* Subtract, Divide
* Successor, Predecessor
* Predicates (e.g. `isZero`, `isEven`, ...)
* (In)equality
* Strings (as lists of characters represented by their char codes)
* Lists (as nested pairs) & list manipulations (e.g. `map`, `reduce`, `filter`)
* ...y'know, all of computation

## Even OOP!

... wait, what?

## FP & OOP: BFFs

### *Object*: 
- receives messages (method name + arguments) 
- gives responses



### *(Lambda) function*: 

- receives input
- returns output


### *Both*: 

* ~~data~~  

* **behavior**

## FP & OOP: BFFs

Smalltalk (iconic OOP language by Kay et al.)

```
class True
  ifTrue: a ifFalse: b
    ^ a value

class False
  ifTrue: a ifFalse: b
    ^ b value
```

Lambda calculus

```
TRUE  := λx.λy.x
FALSE := λx.λy.y
```

This was just a taster...
### Go learn more lambdas! 𝛌🐑

Check out "Fun with Lambdas" by Corey Haines
  * [Upcoming book](https://leanpub.com/fun_with_lambdas)
  * [Talk at GOTO Chicago 2015](https://youtu.be/QPqoFCHpLF4)


#### Here's some other stuff you might like!

* Mary Rose Cook, ["A practical introduction to functional programming"](https://maryrosecook.com/blog/post/a-practical-introduction-to-functional-programming)
* Me, ["Learning Functional Programming in JavaScript"](https://youtu.be/e-5obm1G_FY)
* Alan Kay, ([Message to Smalltalk/Squeak mailing list, 1998](http://wiki.c2.com/?AlanKayOnMessaging))
* William Cook, [“A Proposal for Simplified, Modern Definitions of ‘Object’ and ‘Object Oriented’”](http://wcook.blogspot.fr/2012/07/proposal-for-simplified-modern.html)


### 💙 Merci! 💙

Speaking opportunity courtesy of **JSHeroes**, **MozTechSpeakers**, **Mapbox**

Inspiration courtesy of **Corey Haines** & **Darius Bacon**

Slides courtesy of **[RISE](https://github.com/damianavila/RISE)** & **Jupyter notebook**

Mind-explosion courtesy of **Alonzo Church**
